In [22]:
import pandas as pd
import json

In [23]:
target_df = pd.read_csv("../resources/Clinical-Trial-Parser/data/input/clinical_trials.csv")

In [24]:
target_df.head()

#nct_id                                              title  \
0  NCT04346355  Efficacy of Early Administration of Tocilizuma...   
1  NCT04344951  Chloroquine Phosphate Against Infection by the...   
2  NCT04344444  Treatment in Patients With Suspected or Confir...   
3  NCT04344080  Effect of CytoSorb Adsorber on Hemodynamic and...   
4  NCT04344015                         COVID-19 Plasma Collection   

  has_us_facility                 conditions  \
0           false         COVID-19 Pneumonia   
1           false  Covid-19|Pneumonia, Viral   
2            true                   COVID-19   
3           false                   COVID-19   
4            true                   COVID-19   

                                eligibility_criteria  
0  \n        Inclusion Criteria:\n\n          -  ...  
1  \n        Inclusion Criteria:\n\n          -  ...  
2  \n        Inclusion Criteria:\n\n          -  ...  
3  \n        Inclusion Criteria:\n\n          -  ...  
4  \n        Inclusion Criteria:\n\n          -  ...

In [25]:
input_df = pd.DataFrame(columns = ['#nct_id', 'title', 'has_us_facility', 'conditions',
       'eligibility_criteria'])

# JSONL

In [5]:
with open("../input/trec-ct-json/sample.jsonl", "r") as f:
  trials = [json.loads(trial) for trial in f.read().splitlines()]

In [6]:
trials[0].keys()

dict_keys(['id', 'contents', 'title', 'condition', 'summary', 'detailed_description', 'eligibility'])

In [7]:
for trial in trials:
  input_df = input_df.append({'#nct_id' : trial['id'], 'title' : trial['title'], 'has_us_facility' : True, 'conditions': trial['condition'], 'eligibility_criteria': trial['eligibility']},
        ignore_index = True)

/tmp/ipykernel_45028/4043133524.py:2: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  input_df = input_df.append({'#nct_id' : trial['id'], 'title' : trial['title'], 'has_us_facility' : True, 'conditions': trial['condition'], 'eligibility_criteria': trial['eligibility']},
/tmp/ipykernel_45028/4043133524.py:2: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  input_df = input_df.append({'#nct_id' : trial['id'], 'title' : trial['title'], 'has_us_facility' : True, 'conditions': trial['condition'], 'eligibility_criteria': trial['eligibility']},
/tmp/ipykernel_45028/4043133524.py:2: FutureWarning: In a future version, object-dtype columns with all-bool values will not be included in reductions with bool_only=True. Explicitly cast to bool dtype instead.
  input_df = input_df.append({'#nct_id' : trial['id'], 'title' : trial[

In [8]:
input_df.to_csv("../input/trec-ct-json/sample.csv", index = False)

# IR_Datasets

In [21]:
import ir_datasets
dataset = ir_datasets.load("clinicaltrials/2021/trec-ct-2022")
# namedtuple<doc_id, title, condition, summary, detailed_description, eligibility>
for doc in dataset.docs_iter():
  doc

In [26]:
for idx, doc in enumerate(dataset.docs_iter()):
  input_df = input_df.append({'#nct_id' : doc.doc_id, 'title' : doc.title, 'has_us_facility' : True, 'conditions': doc.condition, 'eligibility_criteria': doc.eligibility},
        ignore_index = True)
  if idx > 10000: break

/tmp/ipykernel_51637/3411851022.py:2: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  input_df = input_df.append({'#nct_id' : doc.doc_id, 'title' : doc.title, 'has_us_facility' : True, 'conditions': doc.condition, 'eligibility_criteria': doc.eligibility},
/tmp/ipykernel_51637/3411851022.py:2: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  input_df = input_df.append({'#nct_id' : doc.doc_id, 'title' : doc.title, 'has_us_facility' : True, 'conditions': doc.condition, 'eligibility_criteria': doc.eligibility},
/tmp/ipykernel_51637/3411851022.py:2: FutureWarning: In a future version, object-dtype columns with all-bool values will not be included in reductions with bool_only=True. Explicitly cast to bool dtype instead.
  input_df = input_df.append({'#nct_id' : doc.doc_id, 'title' : doc.title, 'has_us_facility' : True, 'c

In [28]:
input_df.sample(5)

#nct_id                                              title  \
7750  NCT00038896  Study Evaluating Venlafaxine ER in Adults With...   
9973  NCT00071084  Clinical Trial of HuMax-CD4, a New Drug to Tre...   
8026  NCT00042887  Chemotherapy With or Without Surgery in Treati...   
4001  NCT00004854  The Safety and Efficacy of Adjunct Carvedilol ...   
2212  NCT00002534  Bone Marrow Transplantation in Treating Patien...   

     has_us_facility conditions  \
7750            True              
9973            True              
8026            True              
4001            True              
2212            True              

                                   eligibility_criteria  
7750  \n      \n        Inclusion Criteria:\r\n\r\n ...  
9973  \n      \n        Inclusion criteria\r\n\r\n  ...  
8026  \n      \n        DISEASE CHARACTERISTICS:\r\n...  
4001  \n      \n        Inclusion Criteria:\r\n\r\n ...  
2212  \n      \n        DISEASE CHARACTERISTICS: Acu...

In [29]:
input_df.to_csv("../input/trec-ct-json/sample.csv", index = False)

In [36]:
docstore = dataset.docs_store()

In [41]:
print(docstore.get("NCT00038896").eligibility)


      
        Inclusion Criteria:

          -  A male or female outpatient

          -  Be at least 18 years of age and legal age of consent

          -  Meet DSM-IV criteria for PD (with or without agoraphobia) for at least 3 months before
             study day 1

        Exclusion Criteria:

          -  Treatment with venlafaxine (IR or ER) within 6 months of study day 1

          -  Known hypersensitivity to venlafaxine (IR or ER) or related compounds

          -  History or presence of any clinically important hepatic, renal, or other medical
             disease that might compromise the study or be detrimental to the patient (eg,
             clinically important cardiac arrhythmia, unstable diabetes, carcinoma [except basal
             cell epithelioma], uncontrolled hypertension)
      
    


# Get Documents for the files

In [1]:
import pandas as pd
import numpy as np
import json

with open("../input/trec-ct-json/trec21_content.json", "r") as f:
  docs = json.load(f)

df2021 = pd.read_csv("../input/BM25_KW_2021.txt", sep = " ", names = ["qid", "Q0", "doc_id", "iter", "conf", "run_name"])
df2022 = pd.read_csv("../input/BM25_KW_2022.txt", sep = " ", names = ["qid", "Q0", "doc_id", "iter", "conf", "run_name"])

udoc_ids = np.append(df2021["doc_id"].unique(), df2022["doc_id"].unique())
print(udoc_ids.shape)

doc_dict = {}
for doc in docs:
  doc_dict[doc["id"]] = doc["contents"]

doc_list = []
for doc_id in udoc_ids:
  doc_list.append(doc_dict[doc_id])

res = pd.DataFrame(
  {
    "doc_id": udoc_ids,
    "summary": doc_list
  }
)

res.to_csv("../input/trec-ct-json/trec_KW_data.csv", index = False)

(69525,)
